# Week 7 - Monte-Carlo, Block Averages, NumExpr and Metropolis Algorithm

## From Monte-Carlo to Block Averages

>Let's write a code that calculates $\pi$ with Monte-Carlo sampling and block averages.

We will employ a uniform random distribution $x \in [0,1]$ to calculate $\pi$ with the following integral:

$$ 4\int_0^1 \sqrt{1-x^2} dx$$

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import numexpr as ne

class Integral:
    '''
    This class calculates \pi 
    through Monte Carlo integration
    '''
    
    def __init__(self,N,numexp=False):
        'Initialise the MC.'
        self.N = N
        self.rng = np.random.default_rng(seed=42424)
        self.I = 0.0
        self.I2 = 0.0
        self.stdvn = 0.0
        self.do_block_averages = None
        self.blocks = None
        self.var = None
        self.numexp = numexp
        
    def f(self,x):
        'Function to integrate.'
        return 4.0*np.sqrt(1.0-x**2)
    
    def f2(self,x):
        'Square of self.f, computationally faster.'
        return 16.0*(1.0-x**2)
    
    def compute_mc_integral(self,x):
        'Sample self.f and average.'
        if self.numexp:
            ev = ne.evaluate("(4.0*sqrt(1.0-x**2))",optimization='moderate')
            return np.average(ev)
        else:
            return sum(map(self.f, x))/len(x)

    def compute_mc_integral_var(self,x):
        '''
        Sample self.f and calculates
        mean, mean of the square, variance,
        standard deviation
        '''
        I = self.compute_mc_integral(x)
        I2 = sum(map(self.f2, x))/len(x)
        var = (I2 - I**2)
        stdvn =  np.sqrt((I2 - I**2)/len(x))
        return np.array([I,I2,stdvn,var])
        
    def mc_integral(self,block_averages=False,blocks=1):
        'MC integration driver'
        self.do_block_averages = block_averages
        self.blocks = blocks
        r = self.rng.random(self.N)
        if self.do_block_averages and self.blocks!=self.N:
            rs = np.split(r,self.blocks)
            results = np.array(list(map(self.compute_mc_integral,rs)))
            self.I = np.average(results)
            self.I2 =  np.average(results**2)
            self.stdvn = np.sqrt((self.I2 - self.I**2)/results.shape[0])
            self.var = (self.I2 - self.I**2)
        else:
            self.I,self.I2,self.stdvn,self.var = self.compute_mc_integral_var(r)


In [ ]:
integral = Integral(10000)
integral.mc_integral()
for i in range(5):
    integral.mc_integral()
    print(integral.I)

In [ ]:
y = []
yy = []
x = range(100,200000,1000)
for N in x:
    integral = Integral(N)
    integral.mc_integral()
    y.append(integral.I)
    yy.append(abs(integral.I - np.pi))

In [ ]:
plt.plot(x,y,'o-')
plt.axhline(np.pi,c='k',alpha=0.5)
plt.ylabel('integral')
plt.xlabel('N')

Now we check whether the true error goes down as $1/\sqrt{N}$.

In [ ]:
plt.loglog(x,yy,'o-',label='MC integral error')
plt.loglog(x,list(map(lambda x: 1/np.sqrt(x),x)),label='$\\frac{1}{\sqrt{N}}$')
plt.ylabel('absolute error')
plt.xlabel('N')
plt.legend()

In [ ]:
# Whole data set
N=10000
integral = Integral(N)
integral.mc_integral()
print('I = {:.5f}, variance = {:.5f}, stdvn = {:.5f}, Delta= {:.5f}'.
      format(integral.I,integral.var, integral.stdvn, abs(integral.I-np.pi)))
print('-'*20)
print('sigma_n = {}'.format(integral.stdvn*np.sqrt(N)))
print('sigma_n/sqrt(N) = {}'.format(integral.stdvn))

In [ ]:
#Bloch averages: method 1
N = int(1e4)
l_I = []
l_I2 = []
integral = Integral(N)
NN = 10
for i in range(NN):
    integral.mc_integral()
    print('I = {:.5f}, variance = {:.5f}, stdvn = {:.5f}, Delta= {:.5f}'.format(integral.I,integral.var, 
                                                                integral.stdvn, abs(integral.I-np.pi)))
    l_I.append(integral.I)
    l_I2.append(integral.I**2)
var = np.average(l_I2)-(np.average(l_I))**2
sigma_m = np.sqrt(var)
print('-'*20)
print('sigma_m = {:.5f}'.format(sigma_m))

In [ ]:
#Bloch averages: method 2
N=10000
integral = Integral(N)
integral.mc_integral(block_averages=True,blocks=10)
print('I = {:.5f}, variance = {:.5f}, stdvn = {:.5f}, Delta= {:.5f}'.\
      format(integral.I,integral.var, integral.stdvn, abs(integral.I-np.pi)))
print('-'*20)
print('sigma_s/sqrt(s) = {:.5f}'.format(integral.stdvn))

-------------

# NumExpr

From the project description on PyPI https://pypi.org/project/numexpr/:

>**NumExpr is a fast numerical expression evaluator for NumPy**. 
>
>With it, expressions that operate on arrays (like '3*a+4*b') are accelerated and use less memory than doing the same calculation in Python.
>
>In addition, its multi-threaded capabilities can make use of all your cores – which generally results in substantial performance scaling compared to NumPy.
>
>Last but not least, numexpr can make use of Intel’s VML (Vector Math Library, normally integrated in its Math Kernel Library, or MKL). This allows further acceleration of transcendent expressions

In [ ]:
%load_ext line_profiler
integral = Integral(int(1e6))
%lprun -f Integral.mc_integral integral.mc_integral(block_averages=True,blocks=100)

In [ ]:
%lprun -f Integral.compute_mc_integral integral.mc_integral(block_averages=True,blocks=100)

In [ ]:
integral = Integral(int(1e6),numexp=False)
%timeit integral.mc_integral(block_averages=True,blocks=10)
print(integral.I,integral.stdvn)
integral = Integral(int(1e6),numexp=True)
%timeit integral.mc_integral(block_averages=True,blocks=10)
print(integral.I,integral.stdvn)

Note the speed-up of two orders of magnitued obtained by using ``numexpr``!

In [ ]:
integral = Integral(int(1e6),numexp=True)
%lprun -f Integral.compute_mc_integral integral.mc_integral(block_averages=True,blocks=100)

> The ``NumExpr`` package provides tools for fast evaluation of array expressions. 
It is particularly useful for **large arrays**.

The key to NumExpr’s speed is handling chunks of elements at a time. Default is 4096 elements at a time, using a register machine. NumExpr "sort of" compiles the expression in a vectorized manner and also support multi-threading parallelization by default. Check out the docs at: https://numexpr.readthedocs.io/en/latest/index.html


-----------------------------

## Metropolis Algorithm

Now we will focus on the **Metropolis algorithm**, which has been introduced to you in the lecture of yesterday. In particular, we will sample the distribution

$$P(x) = e^{\frac{-x^2}{2\sigma^2}}.$$

In order to do so, we will create a Python class that runs a Metropolis algorithm reproducing the distribution $P(x)$. We will employ a **Markov chain** obtained through **one random walker** behaving according to the following transition probability:

$$T(x_i \rightarrow x_j) = \min{\left[1,P(x_j)/P(x_i)\right]},$$

where the trial move is obtained with a uniformly distributed random variable $\tilde{x} \in [0,1) $

$$ x_j = x_i + \delta(\tilde{x}-0.5) $$

which is accepted if 

$$\tilde{x}_w \leq w = P(x_j)/P(x_i) = e^{\frac{-(x_j^2-x_i^2)}{2\sigma^2}} $$

with $\tilde{x}_w \in [0,1)$ also being a random variable following a uniform distribution.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

class Metropolis:
    '''
    This class implements 
    the Metropolis algorithm for a Gaussian distribution
    exp(-x**2/(2*sigma**2))
    '''
    
    def __init__(self,N,delta,sigma=1):
        'Initialise the Metropolis'
        self.N = N
        self.rng = np.random.default_rng(seed=42424)
        self.sigma = sigma
        self.delta = delta
        self.pref = -1.0/(2.0*self.sigma**2)
        self.acc = 0
        self.x = 0.0
        self.ar = None
        self.all_x = [self.x]
        self.all_x2 = None
        self.all_x3 = None
        self.all_x4 = None
        self.var = None
        self.counter = 0
        self.autocorr = []
        self.n_autocorr = 10
    
    def metro_step(self):
        'One step of Metropolis'
        rnd = self.rng.random()
        xp = self.x + self.delta * (rnd-0.5)
        p = self.x**2
        pp = xp**2
        w = np.exp(self.pref*(pp-p))
        rnd_w = self.rng.random()
        if (rnd_w<=w):
            self.x = xp 
            self.acc += 1
        self.all_x.append(self.x)
    
    def metro_driver(self):
        'Run N Metropolis steps.'
        for i in range(self.N):
            self.counter += 1
            self.metro_step()
    
    def get_hist(self):
        'Plot Histogram'
        plt.xlabel('x')
        plt.ylabel('count')
        plt.hist(self.all_x,bins=100)
        plt.show()
    
    @staticmethod
    def calc_autocorr(a,N):
        'Autocorrelation function'
        res = np.ones(N)
        for k in range(1,N):
            c_k = np.average(a[:-k]*a[k:]) 
            x_r = np.average(a[:-k])
            x_r_2 = np.average(a[:-k]**2)
            res[k] = (c_k-x_r**2)/(x_r_2-x_r**2)
        return res
    
    def get_stats(self):
        '''
        Calculate, store and print 
        statistical quantities
        '''
        self.ar = self.acc*1.0/self.counter
        self.aver_x = np.average(self.all_x)
        self.aver_x2 = np.average(np.array(self.all_x)**2)
        self.aver_x3 = np.average(np.array(self.all_x)**3)
        self.aver_x4 = np.average(np.array(self.all_x)**4)
        self.var = self.aver_x2-self.aver_x**2
        print("Total number of steps run = {}".format(self.counter))
        print("Acceptance ratio = {}".format(self.ar))
        print("Sigma = {}, delta = {}".format(self.sigma,self.delta))
        print("<x> = {}, <x2> = {}".format(self.aver_x,self.aver_x2))
        print("<x3> = {}, <x4> = {}".format(self.aver_x3,self.aver_x4))
        print("variance = {}".format(self.var))
        
    def get_autocorr(self,n_autocorr=100):
        '''
        Wrapper for the autocorrelation
        function calculator
        '''
        a = np.array(self.all_x)
        self.autocorr = self.calc_autocorr(a,n_autocorr)

Let's run our first Metropolis!

In [ ]:
N= 100000
delta = 5
metro = Metropolis(N,delta)   #Comment to run multiple times
metro.metro_driver()
metro.get_stats()
metro.get_hist()

Let's study the effect of changing N. \
Also, how does the acceptance ratio change if we change $\sigma$?

In [ ]:
metro = Metropolis(10000,5)   
metro.metro_driver()
metro.get_stats()
metro.get_hist()

In [ ]:
x = np.arange(100,50000,100)
y = []
for N in x:
    metro = Metropolis(N,5)
    metro.metro_driver()
    metro.get_stats()
    y.append(1.0-metro.var)

In [ ]:
plt.xlabel('N')
plt.ylabel('$\sigma^2_{true}-\sigma^2_{calc}$')
plt.axhline(0.0,c='grey',alpha=0.5)
plt.axhline(0.05,ls='--',c='grey',alpha=0.5)
plt.axhline(-0.05,ls='--',c='grey',alpha=0.5)
plt.plot(x,y,'o-')
plt.show()